# **HeartView Pipeline for Actiwave Cardio and Other ECG Sources**
## ECG Signal Quality Assessment

This notebook presents an example of the HeartView pipeline's functionalities on some sample ECG data.

### 1. Import Modules

In [13]:
from sys import path
path.append('../')
from heartview import heartview
from heartview.pipeline import ECG, SQA
import pandas as pd
import matplotlib.pyplot as plt

### 2. Load Data

#### 2-a. Load Data of Actiwave Cardio

In [14]:
edf = 'sample_actiwave.edf'
ecg, acc = ECG.read_actiwave(edf)
data = ecg
display(ecg.head(), acc.head())

Timestamp        mV
0 2016-07-20 14:31:00.000000  0.992463
1 2016-07-20 14:31:00.000977  0.995095
2 2016-07-20 14:31:00.001953  0.989246
3 2016-07-20 14:31:00.002930  0.954444
4 2016-07-20 14:31:00.003906  0.921396

Timestamp         X         Y         Z  Magnitude
0 2016-07-20 14:31:00.000000  6.738466  7.041151  1.871547   9.924083
1 2016-07-20 14:31:00.031250  6.738466  6.834366  1.871547   9.778455
2 2016-07-20 14:31:00.062500  6.840360  7.041151  2.162243  10.052046
3 2016-07-20 14:31:00.093750  6.840360  7.041151  2.066343  10.031854
4 2016-07-20 14:31:00.125000  6.738466  6.834366  1.871547   9.778455

#### 2-b. Load Data of Other EEG Sources

In [15]:
file = 'sample_ecg.csv'
data = pd.read_csv(file)
data.head()

Timestamp        mV
0  2016-10-14 10:10:51.000000 -0.206620
1  2016-10-14 10:10:51.000977 -0.197554
2  2016-10-14 10:10:51.001953 -0.186148
3  2016-10-14 10:10:51.002930 -0.197847
4  2016-10-14 10:10:51.003906 -0.190243

### 3. Setup Data

Set the parameters of your data, such as the sampling rate `fs` (Hz) and segment size `seg_size` (seconds).

In [16]:
fs = 1024
seg_size = 60

Segment your data into 60-second windows.

In [17]:
data = heartview.segment_data(data, fs, seg_size)
data

Segment                   Timestamp        mV
0             1  2016-10-14 10:10:51.000000 -0.206620
1             1  2016-10-14 10:10:51.000977 -0.197554
2             1  2016-10-14 10:10:51.001953 -0.186148
3             1  2016-10-14 10:10:51.002930 -0.197847
4             1  2016-10-14 10:10:51.003906 -0.190243
...         ...                         ...       ...
381948        7  2016-10-14 10:17:03.996094 -0.328868
381949        7  2016-10-14 10:17:03.997070 -0.328283
381950        7  2016-10-14 10:17:03.998047 -0.327991
381951        7  2016-10-14 10:17:03.999023 -0.303717
381952        7  2016-10-14 10:17:04.000000 -0.306349

[381953 rows x 3 columns]

### 4. Filter Data

Filter out any 60-Hz powerline interference, baseline wander, and muscle noise.

In [18]:
data['Powerline'] = ECG.powerline_int_filter(data['mV'], fs, q = 20, freq = 60)
data['Filtered'] = ECG.baseline_muscle_filter(data['Powerline'], 0.5, 45, fs, order = 4)
data.head()

Segment                   Timestamp        mV  Powerline  Filtered
0        1  2016-10-14 10:10:51.000000 -0.206620  -0.205123 -0.052997
1        1  2016-10-14 10:10:51.000977 -0.197554  -0.196108 -0.048060
2        1  2016-10-14 10:10:51.001953 -0.186148  -0.184952 -0.043212
3        1  2016-10-14 10:10:51.002930 -0.197847  -0.197073 -0.038543
4        1  2016-10-14 10:10:51.003906 -0.190243  -0.190011 -0.034127

### 5. Assess Signal Quality

##### First, detect the number of peaks (i.e., heartbeats) in each segment of the signal. Save each peak occurrence in a `Peak` column in the data frame.

In [19]:
peak_ix = ECG.detect_rpeaks(data, 'Filtered', fs)
data.loc[peak_ix, 'Peak'] = 1
data.head()

Segment                   Timestamp        mV  Powerline  Filtered  Peak
0        1  2016-10-14 10:10:51.000000 -0.206620  -0.205123 -0.052997   NaN
1        1  2016-10-14 10:10:51.000977 -0.197554  -0.196108 -0.048060   NaN
2        1  2016-10-14 10:10:51.001953 -0.186148  -0.184952 -0.043212   NaN
3        1  2016-10-14 10:10:51.002930 -0.197847  -0.197073 -0.038543   NaN
4        1  2016-10-14 10:10:51.003906 -0.190243  -0.190011 -0.034127   NaN

We can quickly verify that peaks have been detected.

In [20]:
data['Peak'].sum()

807.0

##### Compute second-by-second mean heart rate (HR) and interbeat interval (IBI) values and label all invalid values.

In [21]:
interval_data = ECG.get_seconds(data, 'Peak', fs, seg_size)
interval_data

Segment  Second                   Timestamp     Mean HR    Mean IBI  \
0          1       1  2016-10-14 10:10:51.000000  136.939079  438.151042   
1          1       2  2016-10-14 10:10:52.000000  135.231108  443.684896   
2          1       3  2016-10-14 10:10:53.000000  132.058033  454.345703   
3          1       4  2016-10-14 10:10:54.000000  132.200108  453.857422   
4          1       5  2016-10-14 10:10:55.000000  133.468501  449.544271   
..       ...     ...                         ...         ...         ...   
369        7     370  2016-10-14 10:17:00.000000  130.792975  458.740234   
370        7     371  2016-10-14 10:17:01.000000  128.715084  466.145833   
371        7     372  2016-10-14 10:17:02.000000  130.169492  460.937500   
372        7     373  2016-10-14 10:17:03.000000  130.445860  459.960938   
373        7     374  2016-10-14 10:17:04.000000         NaN         NaN   

     # R Peaks  Invalid  
0          2.0        0  
1          2.0        0  
2          2.0        0  
3          3.0        0  
4          2.0        0  
..         ...      ...  
369        3.0        0  
370        2.0        0  
371        2.0        0  
372        2.0        0  
373        0.0        0  

[374 rows x 7 columns]

##### Compute the SQA metrics by segment.

In [22]:
peaks_by_seg = SQA.evaluate_peaks(interval_data, seg_size)
peaks_by_seg.head()

Segment                   Timestamp  Detected    Expected
0       1  2016-10-14 10:10:51.000000     131.0  133.408152
1       2  2016-10-14 10:11:51.000000     128.0  127.369862
2       3  2016-10-14 10:12:51.000000     128.0  129.086978
3       4  2016-10-14 10:13:51.000000     130.0  128.334239
4       5  2016-10-14 10:14:51.000000     124.0  124.184217

In [23]:
sqa = SQA.compute_metrics(peaks_by_seg)
sqa

Segment                   Timestamp  Detected    Expected  Invalid  \
0       1  2016-10-14 10:10:51.000000     131.0  133.408152        0   
1       2  2016-10-14 10:11:51.000000     128.0  127.369862        0   
2       3  2016-10-14 10:12:51.000000     128.0  129.086978        0   
3       4  2016-10-14 10:13:51.000000     130.0  128.334239        0   
4       5  2016-10-14 10:14:51.000000     124.0  124.184217        0   
5       6  2016-10-14 10:15:51.000000     137.0  137.181144        0   
6       7  2016-10-14 10:16:51.000000      29.0  130.445860        1   

      Missing  % Missing  
0    2.408152   1.805101  
1    0.000000   0.000000  
2    1.086978   0.842051  
3    0.000000   0.000000  
4    0.184217   0.148341  
5    0.181144   0.132047  
6  101.445860  77.768555

## Visualize Data

##### Visualize the raw and filtered ECG signal during Segment 1.

In [24]:
heartview.plot_signal(data, 'Timestamp', ['mV', 'Filtered'], fs, seg_size, segment = 4, signal_type = 'ecg')

##### Visualize the expected-to-missing numbers of beats per segment.

In [25]:
SQA.plot_expected2missing(sqa, title = 'Sample ECG')